In [2]:
import osmnx as ox
import numpy as np
import pandas as pd
import geopandas as gp
import folium
from shapely.geometry import Point, Polygon

In [3]:
import re

def eliminar_tildes(texto):
        texto = re.sub('á','a', texto)
        texto = re.sub('é','e', texto)
        texto = re.sub('í','i', texto)
        texto = re.sub('ó','o', texto)
        texto = re.sub('ú','u', texto)
        texto = re.sub('ñ','n', texto)
        return texto.upper()
    
def arreglar(texto):
    texto = texto.lower()
    texto = texto.replace('.','')
    texto = eliminar_tildes(texto)
    return texto


<p style = "color: blue; font-size :40px;text-align:center;font-family:Times New Roman"> Tarea 3

# 1. [50 puntos] Utilizando las bibliotecas `osmxn` y `folium` realice lo siguiente:

## a) Identifique la ubicación de las sucursales bancarias del Banco Nacional, Banco de Costa Rica, Banco Popular y BAC a lo largo del territorio de Costa Rica.

In [309]:
# Region de la que queremos hacer la busqueda
region = "Costa Rica"
# Criterio de busqueda
etiquetas = {'amenity':"bank"}

resultado = ox.geometries_from_place(query = region, tags = etiquetas)
resultado.columns

/Users/promidat04/opt/anaconda3/lib/python3.9/site-packages/osmnx/geometries.py:805: ShapelyDeprecationWarning: __len__ for multi-part geometries is deprecated and will be removed in Shapely 2.0. Check the length of the `geoms` property instead to get the  number of parts of a multi-part geometry.
  for merged_outer_linestring in list(merged_outer_linestrings):
/Users/promidat04/opt/anaconda3/lib/python3.9/site-packages/osmnx/geometries.py:805: ShapelyDeprecationWarning: Iteration over multi-part geometries is deprecated and will be removed in Shapely 2.0. Use the `geoms` property to access the constituent parts of a multi-part geometry.
  for merged_outer_linestring in list(merged_outer_linestrings):


Index(['amenity', 'name', 'geometry', 'addr:city', 'addr:street', 'atm',
       'phone', 'name:es', 'nodes', 'brand', 'brand:en', 'brand:es',
       'brand:wikidata', 'brand:wikipedia', 'building', 'name:en',
       'official_name', 'official_name:en', 'official_name:es', 'short_name',
       'source', 'drive_through', 'opening_hours', 'operator', 'website',
       'addr:full', 'area', 'alt_name', 'level', 'note', 'addr:postcode',
       'building:levels', 'construction', 'fixme', 'designation', 'name:de',
       'name:it', 'addr:housename', 'int_name', 'layer', 'operator:wikidata',
       'operator:wikipedia', 'addr:place', 'indoor', 'addr:local', 'parts',
       'email', 'buildingpart', 'height', 'wheelchair', 'source_1', 'phone_1',
       'phone_2', 'branch', 'ways', 'type', 'is_in', 'addr:suburb',
       'description', 'addr:housenumber', 'landuse', 'cajero', 'shop',
       'building:colour', 'building:material', 'roof:colour',
       'air_conditioning', 'amenity_1', 'alt_name:en',

In [310]:
bancos = resultado[["name","geometry"]]
bancos

name  \
element_type osmid                             
node         1216928250  Banco de Costa Rica   
             1216933006      Coopeservidores   
             1216938665         Coopealianza   
             3850658798        Western Union   
             4705800690  Banco de Costa Rica   
...                                      ...   
             879780691   Banco de Costa Rica   
             3728651531      Coopeservidores   
             6757609847         Coopealianza   
             6852650131         Grupo Mutual   
way          428375535         Banco Popular   

                                                                  geometry  
element_type osmid                                                          
node         1216928250                         POINT (-85.61129 11.21112)  
             1216933006                         POINT (-85.62927 11.07378)  
             1216938665                         POINT (-85.63495 11.07487)  
             3850658798                         POINT (-85.63499 11.07483)  
             4705800690                         POINT (-85.63368 11.07213)  
...                                                                    ...  
             879780691                           POINT (-82.83936 8.53474)  
             3728651531                          POINT (-82.94353 8.64758)  
             6757609847                          POINT (-82.91023 8.44386)  
             6852650131                          POINT (-82.94348 8.64779)  
way          428375535   POLYGON ((-82.94348 8.64971, -82.94313 8.64968...  

[877 rows x 2 columns]

In [311]:
import folium
# coordenadas de Costa Rica 9.934598, -84.094154
m = folium.Map(location=[9.933333,  -84.083333], zoom_start = 13)
folium.TileLayer('CartoDB positron').add_to(m)
display(m)

In [312]:
#elimino NaN
bancos = bancos.dropna()

In [313]:
bancos = bancos[bancos.name.str.match("(Banco Nacional|BAC|Banco de Costa Rica|Banco Popular)")] 
bancos

name  \
element_type osmid                             
node         1216928250  Banco de Costa Rica   
             4705800690  Banco de Costa Rica   
way          302006416        Banco Nacional   
             381870071         Banco Popular   
             285165896   Banco de Costa Rica   
...                                      ...   
node         1439016818       Banco Nacional   
             814344073        Banco Nacional   
             814479585        Banco Nacional   
             879780691   Banco de Costa Rica   
way          428375535         Banco Popular   

                                                                  geometry  
element_type osmid                                                          
node         1216928250                         POINT (-85.61129 11.21112)  
             4705800690                         POINT (-85.63368 11.07213)  
way          302006416   POLYGON ((-85.62958 11.07031, -85.62956 11.070...  
             381870071   POLYGON ((-85.63426 11.07207, -85.63407 11.072...  
             285165896   POLYGON ((-85.78268 10.43167, -85.78272 10.431...  
...                                                                    ...  
node         1439016818                          POINT (-82.91224 8.81970)  
             814344073                           POINT (-82.91044 8.44287)  
             814479585                           POINT (-82.94352 8.64729)  
             879780691                           POINT (-82.83936 8.53474)  
way          428375535   POLYGON ((-82.94348 8.64971, -82.94313 8.64968...  

[436 rows x 2 columns]

In [314]:
for geom, nombre in zip(bancos.geometry, bancos.name):
  edificio = folium.GeoJson(data = geom).add_to(m) # agregar edificio
  etiqueta = folium.Popup(nombre).add_to(edificio) # agregar etiqueta
    
display(m)

## b) Utilizando la biblioteca `folium` cree un mapa interactivo que permita ver las diferentes sucursales bancarias diferenciadas por su color.

In [315]:
bancos["x"] = bancos.centroid.x
bancos["y"] = bancos.centroid.y
bancos[["x","y"]]

/var/folders/2p/yndl9k2n4kd5csrt0b9hz2ww0000gn/T/ipykernel_13576/4274385975.py:1: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  bancos["x"] = bancos.centroid.x
/var/folders/2p/yndl9k2n4kd5csrt0b9hz2ww0000gn/T/ipykernel_13576/4274385975.py:2: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  bancos["y"] = bancos.centroid.y


x          y
element_type osmid                           
node         1216928250 -85.611292  11.211121
             4705800690 -85.633679  11.072130
way          302006416  -85.629489  11.070238
             381870071  -85.634132  11.072004
             285165896  -85.782619  10.431575
...                            ...        ...
node         1439016818 -82.912240   8.819700
             814344073  -82.910437   8.442870
             814479585  -82.943522   8.647289
             879780691  -82.839358   8.534740
way          428375535  -82.943316   8.649570

[436 rows x 2 columns]

In [316]:
bancos.loc[bancos.name.astype(str).str.contains('BAC'),'name'] = 'BAC'
bancos.loc[bancos.name.astype(str).str.contains('Banco.*Costa Rica|BCR'),'name'] = 'Banco de Costa Rica'
bancos.loc[bancos.name.astype(str).str.contains('Banco Popular'),'name'] = 'Banco Popular'
bancos.loc[bancos.name.astype(str).str.contains('Banco Nacional|BN'),'name'] = 'Banco Nacional'

In [317]:
estilos = {
  "Banco de Costa Rica":{"color":"red"},
  "Banco Nacional":{"color":"blue"},
    "Banco Popular":{"color":"green"},
    "BAC":{"color":"yellow"}
}


In [318]:
bancos.name.unique()

array(['Banco de Costa Rica', 'Banco Nacional', 'Banco Popular', 'BAC'],
      dtype=object)

In [319]:

for bancos in bancos.itertuples():
  estilo = estilos[bancos.name]
  c = folium.Marker(location=[bancos.y,bancos.x], popup = bancos.name,
                    icon = folium.Icon(color = estilo["color"])).add_to(m)

m

/var/folders/2p/yndl9k2n4kd5csrt0b9hz2ww0000gn/T/ipykernel_13576/3810276875.py:4: UserWarning: color argument of Icon should be one of: {'blue', 'lightred', 'cadetblue', 'darkpurple', 'darkgreen', 'black', 'darkred', 'beige', 'purple', 'lightgray', 'lightblue', 'pink', 'darkblue', 'orange', 'red', 'lightgreen', 'white', 'gray', 'green'}.
  icon = folium.Icon(color = estilo["color"])).add_to(m)


## c) Utilizando la biblioteca `folium` cree un mapa interactivo que permita ver la cantidad de sucursales bancarias en cada uno de los cantones.

In [320]:
cantones = gp.read_file("../datos/geo_data/cantones/cantones.shp")
cantones.head()

provincia        canton  poblacion      area_k2  \
0  Puntarenas    Corredores    51291.0   623.723527   
1  Puntarenas       Golfito    44572.0  1750.056183   
2  Puntarenas     Coto Brus    44176.0   944.175405   
3  Puntarenas           Osa    30818.0  1922.774483   
4  Puntarenas  Buenos Aires    52126.0  2382.972927   

                                            geometry  
0  POLYGON ((-82.90137 8.72708, -82.90033 8.72265...  
1  MULTIPOLYGON (((-83.46660 8.68827, -83.46669 8...  
2  POLYGON ((-82.96647 9.09421, -82.96337 9.09420...  
3  POLYGON ((-83.83946 9.25534, -83.83642 9.25533...  
4  POLYGON ((-83.32101 9.38409, -83.31462 9.38327...

In [321]:
bancos_puntos = resultado[[True if bancos.__class__.__name__ == "Point" else False for bancos in resultado.geometry]]

In [322]:
bancos_puntos['x'] = bancos_puntos['geometry'].x
bancos_puntos['y'] = bancos_puntos['geometry'].y

bancos_puntos[["name", "x","y"]].head(15)

/Users/promidat04/opt/anaconda3/lib/python3.9/site-packages/geopandas/geodataframe.py:1351: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  super().__setitem__(key, value)


name          x          y
element_type osmid                                                 
node         1216928250   Banco de Costa Rica -85.611292  11.211121
             1216933006       Coopeservidores -85.629265  11.073783
             1216938665          Coopealianza -85.634950  11.074872
             3850658798         Western Union -85.634985  11.074833
             4705800690   Banco de Costa Rica -85.633679  11.072130
             3944970146              National -85.790141  10.439539
             6841410514             Banco BCT -85.592828  10.557569
             1416827859   Banco de Costa Rica -85.840884  10.299265
             1416827864        Banco Nacional -85.841135  10.299191
             1416840798  Scotiabank Tamarindo -85.830954  10.308842
             1416880273              Citibank -85.830775  10.309509
             3954366792         Western Union -85.841182  10.299170
             6841557704        BAC Credomatic -85.840808  10.299165
             4748104271         Banco Popular -85.664805   9.945123
             3042693649        Banco Nacional -85.169051  10.823264

In [323]:
from shapely.geometry import Point, Polygon

bancos_puntos["geometry"] = [Point(x,y) for x,y in zip(bancos_puntos.x, bancos_puntos.y)]

#contamos los puntos
resultado = []
for canton in cantones.geometry:
  conteo = sum([canton.contains(punto) for punto in bancos_puntos["geometry"]])
  resultado.append(conteo)
    
cantones["cantidad_bancos"] = resultado

cantones[["canton","cantidad_bancos"]].head(15)

/Users/promidat04/opt/anaconda3/lib/python3.9/site-packages/geopandas/geodataframe.py:1351: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  super().__setitem__(key, value)


canton  cantidad_bancos
0           Corredores                7
1              Golfito                5
2            Coto Brus                4
3                  Osa                4
4         Buenos Aires                3
5        Pérez Zeledón               12
6               Quepos                5
7            Talamanca                2
8              Parrita                0
9              Tarrazú                0
10                Dota                1
11            Garabito                6
12  León Cortés Castro                1
13            Puriscal                1
14              Aserrí                4

In [324]:
import folium
# coordenadas de Costa Rica 9.934598, -84.094154
m = folium.Map(location=[9.933333,  -84.083333], zoom_start = 13)
folium.TileLayer('CartoDB positron').add_to(m)


In [325]:
choropleth = folium.Choropleth(
 geo_data = cantones,
 data = cantones,
 columns = ["canton","cantidad_bancos"],
 key_on = "feature.properties.canton",
 fill_color = 'OrRd',
 highlight = True).add_to(m)
 
choropleth.geojson.add_child(
    folium.features.GeoJsonTooltip(['canton','cantidad_bancos'], labels=False)
).add_to(m)

display(m)

## d) Realice una interpretación de los resultados obtenidos.

# 2. [50 puntos] Utilizando el conjunto de datos base de datos `IPS_cantonal.xlsx` realice lo siguiente:

In [302]:
datos = pd.read_excel(io = "../datos/base-de-datos-IPS-cantonal.xlsx")

datos1 = datos[["Cantón",'Índice de Progreso Social']]
datos1['Cantón'] = [arreglar(x) for x in datos1['Cantón']]
datos1.rename(columns = {'Cantón':'canton'}, inplace = True)
datos1.head()

/Users/promidat04/opt/anaconda3/lib/python3.9/site-packages/openpyxl/worksheet/_reader.py:312: UserWarning: Unknown extension is not supported and will be removed
  warn(msg)
/var/folders/2p/yndl9k2n4kd5csrt0b9hz2ww0000gn/T/ipykernel_13576/3638783506.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  datos1['Cantón'] = [arreglar(x) for x in datos1['Cantón']]
/Users/promidat04/opt/anaconda3/lib/python3.9/site-packages/pandas/core/frame.py:5039: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  return super().rename(


canton  Índice de Progreso Social
0      SAN JOSE                  70.403172
1        ESCAZU                  78.040103
2  DESAMPARADOS                  73.489666
3      PURISCAL                  78.876918
4       TARRAZU                  74.302259

In [303]:
cantones['canton'] = [arreglar(x) for x in cantones['canton']]
cantones.head()

provincia        canton  poblacion      area_k2  \
0  Puntarenas    CORREDORES    51291.0   623.723527   
1  Puntarenas       GOLFITO    44572.0  1750.056183   
2  Puntarenas     COTO BRUS    44176.0   944.175405   
3  Puntarenas           OSA    30818.0  1922.774483   
4  Puntarenas  BUENOS AIRES    52126.0  2382.972927   

                                            geometry  cantidad_bancos  
0  POLYGON ((-82.90137 8.72708, -82.90033 8.72265...                7  
1  MULTIPOLYGON (((-83.46660 8.68827, -83.46669 8...                5  
2  POLYGON ((-82.96647 9.09421, -82.96337 9.09420...                4  
3  POLYGON ((-83.83946 9.25534, -83.83642 9.25533...                4  
4  POLYGON ((-83.32101 9.38409, -83.31462 9.38327...                3

## a) Utilizando la biblioteca `folium` diseñe un mapa interactivo que permita identifica como se comporta la variable Indice de Progreso Social en los diferentes cantones.

In [304]:
df = cantones.merge(datos1,how = "left")
df.head(15)

provincia              canton  poblacion      area_k2  \
0   Puntarenas          CORREDORES    51291.0   623.723527   
1   Puntarenas             GOLFITO    44572.0  1750.056183   
2   Puntarenas           COTO BRUS    44176.0   944.175405   
3   Puntarenas                 OSA    30818.0  1922.774483   
4   Puntarenas        BUENOS AIRES    52126.0  2382.972927   
5     San José       PEREZ ZELEDON   142789.0  1901.393446   
6   Puntarenas              QUEPOS    32121.0   559.010331   
7        Limón           TALAMANCA    41518.0  2814.658267   
8   Puntarenas             PARRITA    19457.0   479.629981   
9     San José             TARRAZU    18264.0   290.111618   
10    San José                DOTA     7846.0   405.833655   
11  Puntarenas            GARABITO    24737.0   315.381452   
12    San José  LEON CORTES CASTRO    13493.0   121.938260   
13    San José            PURISCAL    37345.0   554.985169   
14    San José              ASERRI    62477.0   168.425499   

                                             geometry  cantidad_bancos  \
0   POLYGON ((-82.90137 8.72708, -82.90033 8.72265...                7   
1   MULTIPOLYGON (((-83.46660 8.68827, -83.46669 8...                5   
2   POLYGON ((-82.96647 9.09421, -82.96337 9.09420...                4   
3   POLYGON ((-83.83946 9.25534, -83.83642 9.25533...                4   
4   POLYGON ((-83.32101 9.38409, -83.31462 9.38327...                3   
5   POLYGON ((-83.77329 9.59825, -83.77217 9.59826...               12   
6   POLYGON ((-84.13572 9.57168, -84.13337 9.57091...                5   
7   POLYGON ((-82.89452 9.76752, -82.89216 9.76713...                2   
8   POLYGON ((-84.30298 9.64969, -84.30067 9.64754...                0   
9   POLYGON ((-83.98178 9.71802, -83.97882 9.71819...                0   
10  POLYGON ((-83.98595 9.73927, -83.98254 9.73711...                1   
11  POLYGON ((-84.67583 9.87729, -84.67448 9.87743...                6   
12  POLYGON ((-84.09415 9.74942, -84.09264 9.74917...                1   
13  POLYGON ((-84.40184 9.90958, -84.40088 9.90939...                1   
14  POLYGON ((-84.08014 9.87557, -84.07916 9.87509...                4   

    Índice de Progreso Social  
0                   69.165013  
1                   67.931809  
2                   71.172839  
3                   67.624872  
4                   69.989766  
5                   74.427587  
6                   68.591365  
7                   61.662161  
8                   67.495929  
9                   74.302259  
10                  76.336568  
11                  65.428580  
12                  77.115197  
13                  78.876918  
14                  72.560657

In [305]:
import folium
# coordenadas de Costa Rica 9.934598, -84.094154
m = folium.Map(location=[9.933333,  -84.083333], zoom_start = 13)
folium.TileLayer('CartoDB positron').add_to(m)


In [306]:
choropleth = folium.Choropleth(
 geo_data = df,
 data = df,
 columns = ["canton","Índice de Progreso Social"],
 key_on = "feature.properties.canton",
 fill_color = 'OrRd',
 highlight = True).add_to(m)
 
choropleth.geojson.add_child(
    folium.features.GeoJsonTooltip(['canton','Índice de Progreso Social'], labels=False)
).add_to(m)
m

## b) Seleccione una región y una variable de su interés y creee un mapa interactivo que permita observar el comportamiento de la variable.

In [289]:
datos1 = datos[["Cantón",'Esperanza de vida al nacer']]
datos1['Cantón'] = [arreglar(x) for x in datos1['Cantón']]
datos1.rename(columns = {'Cantón':'canton'}, inplace = True)
datos1.head()

/var/folders/2p/yndl9k2n4kd5csrt0b9hz2ww0000gn/T/ipykernel_13576/2771134960.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  datos1['Cantón'] = [arreglar(x) for x in datos1['Cantón']]
/Users/promidat04/opt/anaconda3/lib/python3.9/site-packages/pandas/core/frame.py:5039: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  return super().rename(


canton  Esperanza de vida al nacer
0      SAN JOSE                      78.751
1        ESCAZU                      78.048
2  DESAMPARADOS                      79.089
3      PURISCAL                      82.038
4       TARRAZU                      76.756

In [290]:
df = cantones.merge(datos1,how = "left")
df.head(15)

provincia              canton  poblacion      area_k2  \
0   Puntarenas          CORREDORES    51291.0   623.723527   
1   Puntarenas             GOLFITO    44572.0  1750.056183   
2   Puntarenas           COTO BRUS    44176.0   944.175405   
3   Puntarenas                 OSA    30818.0  1922.774483   
4   Puntarenas        BUENOS AIRES    52126.0  2382.972927   
5     San José       PEREZ ZELEDON   142789.0  1901.393446   
6   Puntarenas              QUEPOS    32121.0   559.010331   
7        Limón           TALAMANCA    41518.0  2814.658267   
8   Puntarenas             PARRITA    19457.0   479.629981   
9     San José             TARRAZU    18264.0   290.111618   
10    San José                DOTA     7846.0   405.833655   
11  Puntarenas            GARABITO    24737.0   315.381452   
12    San José  LEON CORTES CASTRO    13493.0   121.938260   
13    San José            PURISCAL    37345.0   554.985169   
14    San José              ASERRI    62477.0   168.425499   

                                             geometry  cantidad_bancos  \
0   POLYGON ((-82.90137 8.72708, -82.90033 8.72265...                7   
1   MULTIPOLYGON (((-83.46660 8.68827, -83.46669 8...                5   
2   POLYGON ((-82.96647 9.09421, -82.96337 9.09420...                4   
3   POLYGON ((-83.83946 9.25534, -83.83642 9.25533...                4   
4   POLYGON ((-83.32101 9.38409, -83.31462 9.38327...                3   
5   POLYGON ((-83.77329 9.59825, -83.77217 9.59826...               12   
6   POLYGON ((-84.13572 9.57168, -84.13337 9.57091...                5   
7   POLYGON ((-82.89452 9.76752, -82.89216 9.76713...                2   
8   POLYGON ((-84.30298 9.64969, -84.30067 9.64754...                0   
9   POLYGON ((-83.98178 9.71802, -83.97882 9.71819...                0   
10  POLYGON ((-83.98595 9.73927, -83.98254 9.73711...                1   
11  POLYGON ((-84.67583 9.87729, -84.67448 9.87743...                6   
12  POLYGON ((-84.09415 9.74942, -84.09264 9.74917...                1   
13  POLYGON ((-84.40184 9.90958, -84.40088 9.90939...                1   
14  POLYGON ((-84.08014 9.87557, -84.07916 9.87509...                4   

    Esperanza de vida al nacer  
0                       76.367  
1                       76.246  
2                       80.899  
3                       74.816  
4                       80.309  
5                       79.055  
6                       76.462  
7                       75.631  
8                       77.349  
9                       76.756  
10                      78.889  
11                      78.357  
12                      80.199  
13                      82.038  
14                      77.794

In [298]:
import folium
# coordenadas de Costa Rica 9.934598, -84.094154
m = folium.Map(location=[9.933333,  -84.083333], zoom_start = 13)
folium.TileLayer('CartoDB positron').add_to(m)


In [299]:
choropleth = folium.Choropleth(
 geo_data = df,
 data = df,
 columns = ["canton","Esperanza de vida al nacer"],
 key_on = "feature.properties.canton",
 fill_color = 'YlGnBu',
 highlight = True).add_to(m)

folium.LayerControl().add_to(m)

choropleth.geojson.add_child(
    folium.features.GeoJsonTooltip(['canton','Esperanza de vida al nacer'], labels=False)
).add_to(m)
m

## c) Realice una interpretación de los resultados.

# 3. [30 puntos] Utilizando la biblioteca `altair` y la tabla de datos `movies` de la biblioteca `vega_datasets` realice lo siguiente:

In [3]:
import altair as alt
from vega_datasets import data

movies =data.movies()
movies = movies[["Release_Date","Title","Major_Genre","Rotten_Tomatoes_Rating","Production_Budget"]]
movies.Title = movies.Title.astype(str)
movies.Release_Date = pd.to_datetime(movies.Release_Date)
movies = movies.dropna()
# movies = movies.query('19800101 < Release_Date < 20100101')            

## a) Diseñe un gráfico que permita analizar el presupuesto por año en cada uno de los géneros cinematográficos.

In [5]:
movies

Release_Date                       Title        Major_Genre  \
3      1998-09-11        Let's Talk About Sex             Comedy   
4      1998-10-09                        Slam              Drama   
11     1968-12-11                     Oliver!            Musical   
21     1972-11-09                        1776              Drama   
22     1979-12-14                        1941             Comedy   
...           ...                         ...                ...   
3196   2008-10-31  Zack and Miri Make a Porno             Comedy   
3197   2007-03-02                      Zodiac  Thriller/Suspense   
3198   2006-08-11                        Zoom          Adventure   
3199   2005-10-28         The Legend of Zorro          Adventure   
3200   1998-07-17           The Mask of Zorro          Adventure   

      Rotten_Tomatoes_Rating  Production_Budget  
3                       13.0           300000.0  
4                       62.0          1000000.0  
11                      84.0         10000000.0  
21                      57.0          4000000.0  
22                      33.0         32000000.0  
...                      ...                ...  
3196                    65.0         24000000.0  
3197                    89.0         85000000.0  
3198                     3.0         35000000.0  
3199                    26.0         80000000.0  
3200                    82.0         65000000.0  

[2186 rows x 5 columns]

## b) Utilizando la biblioteca `altair` replique el diseño del punto anterior.

In [7]:
alt.Chart(movies,
                 title = "Relación año y presupuesto de producción."
                 ).mark_line(point = { "size": 80},
                             strokeWidth = 5,
                             color = "#c67ace").encode(
    x = alt.X('year(Release_Date):T', title = "fecha"),
    y = alt.Y('sum(Production_Budget):Q', 
              title = "presupuesto",
              scale = alt.Scale(zero = False, type = "log")),
    color = alt.Color('Major_Genre', 
                      legend = alt.Legend(title = "Género principal")),
    tooltip = ['year(Release_Date):T',
               'min(Production_Budget):Q',
               'mean(Production_Budget):Q',
               'median(Production_Budget):Q',
               'max(Production_Budget):Q']).properties(width=650, height=400
    ).interactive()

alt.Chart(...)

## c) Interprete los resultados.

## d) Diseñe un gráfico que permita analizar la variedad de géneros cinematográficos tomando para la comparación el primero año de cada década.

In [12]:
decada = (movies["Release_Date"].dt.year //10)*10

movies["decada"] = decada

movies.decada = pd.to_datetime(movies.decada,format='%Y')

In [27]:
movies["decada"].dt.year

3       1990
4       1990
11      1960
21      1970
22      1970
        ... 
3196    2000
3197    2000
3198    2000
3199    2000
3200    1990
Name: decada, Length: 2186, dtype: int64

## e) Utilizando la biblioteca `altair` replique el diseño del punto anterior.

In [31]:
alt.Chart(movies, 
                 title = "Peliculas publicadas por año según su género"
                 ).mark_area().encode(
    x = alt.X('year(decada):O', title = "Año"),
    y = alt.Y('count(Major_Genre):Q',
              title='Cantidad de películas',
              stack="normalize"),
    color = alt.Color("Major_Genre", title = "Género")).properties(width=650, height=400
    )

alt.Chart(...)

## f) Interprete los resultados.